In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import dgl
from dgl.nn import ChebConv
import networkx as nx
import networkx.algorithms.community as nx_comm
import numpy as np
import pandas as pd
import numpy.linalg as alg
import os
from tqdm import tqdm
from functools import reduce
import argparse


def node_connects_cluster(node):
    return set(map(lambda x: inverse_cluster_dict[x], list(g[node]))).union(set([inverse_cluster_dict[node]]))


def po_linear_model(graph, alpha=1, beta=1, sigma=0.1, gamma=2):    
    for i in graph.nodes:
        graph.nodes[i]["y"] = alpha + beta * graph.nodes[i]["z"] + sigma * np.random.normal() +  gamma * sum([graph.nodes[ngbr]['z'] for ngbr in graph[i]])/graph.degree[i]  

def po_multiplicative_model(graph, alpha=1, sigma=0.1, delta=1, gamma=2): 
    for i in graph.nodes:
        graph.nodes[i]["y"] = ( (alpha + sigma * np.random.normal()) * graph.degree[i]/avg_deg )  *  (1 + delta * graph.nodes[i]["z"] + gamma * sum([graph.nodes[ngbr]['z'] for ngbr in graph[i]]) / len(graph[i]) )



DGL backend not selected or invalid.  Assuming PyTorch for now.


Setting the default backend to "pytorch". You can change it in the ~/.dgl/config.json file or export the DGLBACKEND environment variable.  Valid options are: pytorch, mxnet, tensorflow (all lowercase)


/root/miniconda3/envs/myconda/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:

path = 'Dataset/socfb-Stanford3.mtx'

df = pd.read_table(path, skiprows=1, names = ["source", "target"], sep=" ")
g = nx.from_pandas_edgelist(df)

# calculate basic elements
num_nodes = g.number_of_nodes()
num_edges = g.number_of_edges()
degs = [g.degree[i] for i in g.nodes]
avg_deg = sum(degs)/len(degs)

res = 10


# clustering
# generally, we fix the outcome of clustering
clusters = nx_comm.louvain_communities(g, seed = 10, resolution=res)
clusters = sorted(clusters, key = len, reverse=True)
cluster_sizes = list(map(len, clusters))
num_cluster = len(clusters)

# dict: from node to its cluster
inverse_cluster_dict = {
    node: cl for cl in range(num_cluster) for node in clusters[cl]
}

# dict: from node to its connected cluster
node_to_connected_clusters = {
    node: node_connects_cluster(node) for node in range(1, num_nodes + 1)
}


for i in g.nodes:
    g.nodes[i]["n_cl"] = len(node_to_connected_clusters[i])
    g.nodes[i]["deg"] = g.degree[i]

rev_cluster_sizes = cluster_sizes[::-1]
rev_clusters = clusters[::-1]
rev_cluster_sizes = np.array(rev_cluster_sizes)


In [3]:
dgl_G = dgl.from_networkx(g)

In [4]:
ramps = [0.02, 0.05, 0.1, 0.25, 0.5]
repeat_num = 1000

In [5]:

class GCN(nn.Module):
    def __init__(self):
        super().__init__()
        self.conv1 = dgl.nn.ChebConv(2, 16, 2)
        self.conv2 = dgl.nn.ChebConv(16, 16, 1)
        self.conv3 = dgl.nn.ChebConv(16, 1, 1)
        
    def forward(self, g, features):
        x = self.conv1(g, features)
        x = self.conv2(g, x)
        x = self.conv3(g, x)
        return x
        

In [ ]:
# cluster-level cr

GATE_hat_list = np.zeros((repeat_num, len(ramps)))

for seed in tqdm(range(repeat_num)):    
    np.random.seed(seed)     
    rollout_index = np.random.uniform(0, 1, size=(num_nodes,))   
    
    for num_step in range(len(ramps)): 
        print(f"Seed: {seed}")
        torch.manual_seed(2)
        p_list = ramps[num_step:]                
        g_feat_list = []
        y_list = []        
        for p in p_list:            
            z = (rollout_index < np.quantile(rollout_index, p))
            
            nx.set_node_attributes(g, 0, "z")
            nx.set_node_attributes(g, {unit:1 for unit in range(num_nodes) if z[unit]}, "z")            
                        
            po_multiplicative_model(g, gamma = 1)            
            g_feat_list.append(torch.tensor([[g.nodes[n]['z'], g.nodes[n]['deg']] for n in g.nodes], dtype=torch.float))
            y_list.append(torch.tensor([[g.nodes[n]['y']] for n in g.nodes], dtype=torch.float).reshape(-1))
    
        # Instantiate the model and optimizer
        model = GCN()    
        optimizer = torch.optim.Adam(model.parameters(), lr=0.004)
            
        # Train the model
        for epoch in range(400):
            for i in range(len(p_list)):
                model.train()
                optimizer.zero_grad()
                out = model(dgl_G, g_feat_list[i])
                loss = F.mse_loss(out.squeeze(), y_list[i])  
                loss.backward()
                optimizer.step()
            
                if epoch % 50 == 0:
                    print(f'Epoch {epoch}, Treat Prop: {p_list[i]:.2f}, Loss: {loss:.4f}')
    
        print(loss.item())
        g_feat = g_feat_list[0]
    
        g_feat[:,0] = 0
        global_control_pred = model(dgl_G, g_feat).detach().numpy()
    
        g_feat[:,0] = 1
        global_treat_pred = model(dgl_G, g_feat).detach().numpy()
    
        GATE_hat = global_treat_pred.mean() - global_control_pred.mean()
    
        GATE_hat_list[seed, num_step] = GATE_hat
        
    torch.save(GATE_hat_list, "Result/Multiplicative_CR_unit.pkl")


  0%|          | 0/1000 [00:00<?, ?it/s]

Seed: 0


/root/miniconda3/envs/myconda/lib/python3.10/site-packages/dgl/nn/pytorch/conv/chebconv.py:108: DGLWarning: lambda_max is not provided, using default value of 2.  Please use dgl.laplacian_lambda_max to compute the eigenvalues.
  dgl_warning(


Epoch 0, Treat Prop: 0.02, Loss: 4.3807
Epoch 0, Treat Prop: 0.05, Loss: 0.6538
Epoch 0, Treat Prop: 0.10, Loss: 1.4452
Epoch 0, Treat Prop: 0.25, Loss: 3.6972
Epoch 0, Treat Prop: 0.50, Loss: 7.1328
Epoch 50, Treat Prop: 0.02, Loss: 0.2762
Epoch 50, Treat Prop: 0.05, Loss: 0.2817
Epoch 50, Treat Prop: 0.10, Loss: 0.2464
Epoch 50, Treat Prop: 0.25, Loss: 0.4162
Epoch 50, Treat Prop: 0.50, Loss: 1.4122
Epoch 100, Treat Prop: 0.02, Loss: 0.2236
Epoch 100, Treat Prop: 0.05, Loss: 0.2442
Epoch 100, Treat Prop: 0.10, Loss: 0.1908
Epoch 100, Treat Prop: 0.25, Loss: 0.3133
Epoch 100, Treat Prop: 0.50, Loss: 1.1117
Epoch 150, Treat Prop: 0.02, Loss: 0.0762
Epoch 150, Treat Prop: 0.05, Loss: 0.1062
Epoch 150, Treat Prop: 0.10, Loss: 0.1029
Epoch 150, Treat Prop: 0.25, Loss: 0.1116
Epoch 150, Treat Prop: 0.50, Loss: 0.3906
Epoch 200, Treat Prop: 0.02, Loss: 0.0627
Epoch 200, Treat Prop: 0.05, Loss: 0.0689
Epoch 200, Treat Prop: 0.10, Loss: 0.0581
Epoch 200, Treat Prop: 0.25, Loss: 0.1199
Epoch 2

  0%|          | 1/1000 [00:32<8:54:11, 32.08s/it]

...

0.189146488904953
Seed: 811
Epoch 0, Treat Prop: 0.02, Loss: 4.3562
Epoch 0, Treat Prop: 0.05, Loss: 0.6504
Epoch 0, Treat Prop: 0.10, Loss: 1.5278
Epoch 0, Treat Prop: 0.25, Loss: 3.6777
Epoch 0, Treat Prop: 0.50, Loss: 6.8464
Epoch 50, Treat Prop: 0.02, Loss: 0.2740
Epoch 50, Treat Prop: 0.05, Loss: 0.2912
Epoch 50, Treat Prop: 0.10, Loss: 0.2568
Epoch 50, Treat Prop: 0.25, Loss: 0.4305
Epoch 50, Treat Prop: 0.50, Loss: 1.3402
Epoch 100, Treat Prop: 0.02, Loss: 0.2152
Epoch 100, Treat Prop: 0.05, Loss: 0.2408
Epoch 100, Treat Prop: 0.10, Loss: 0.1912
Epoch 100, Treat Prop: 0.25, Loss: 0.3223
Epoch 100, Treat Prop: 0.50, Loss: 1.0221
Epoch 150, Treat Prop: 0.02, Loss: 0.1023
Epoch 150, Treat Prop: 0.05, Loss: 0.1257
Epoch 150, Treat Prop: 0.10, Loss: 0.0798
Epoch 150, Treat Prop: 0.25, Loss: 0.1709
Epoch 150, Treat Prop: 0.50, Loss: 0.3756
Epoch 200, Treat Prop: 0.02, Loss: 0.0635
Epoch 200, Treat Prop: 0.05, Loss: 0.0587
Epoch 200, Treat Prop: 0.10, Loss: 0.0721
Epoch 200, Treat Prop

 81%|████████  | 812/1000 [6:53:42<1:33:17, 29.77s/it]

0.23995603621006012
Seed: 812
Epoch 0, Treat Prop: 0.02, Loss: 4.3633
Epoch 0, Treat Prop: 0.05, Loss: 0.6746
Epoch 0, Treat Prop: 0.10, Loss: 1.4864
Epoch 0, Treat Prop: 0.25, Loss: 3.6770
Epoch 0, Treat Prop: 0.50, Loss: 7.0262
Epoch 50, Treat Prop: 0.02, Loss: 0.2633
Epoch 50, Treat Prop: 0.05, Loss: 0.2810
Epoch 50, Treat Prop: 0.10, Loss: 0.2421
Epoch 50, Treat Prop: 0.25, Loss: 0.4203
Epoch 50, Treat Prop: 0.50, Loss: 1.3615
Epoch 100, Treat Prop: 0.02, Loss: 0.2090
Epoch 100, Treat Prop: 0.05, Loss: 0.2404
Epoch 100, Treat Prop: 0.10, Loss: 0.1828
Epoch 100, Treat Prop: 0.25, Loss: 0.3165
Epoch 100, Treat Prop: 0.50, Loss: 1.0579
Epoch 150, Treat Prop: 0.02, Loss: 0.0940
Epoch 150, Treat Prop: 0.05, Loss: 0.1145
Epoch 150, Treat Prop: 0.10, Loss: 0.0660
Epoch 150, Treat Prop: 0.25, Loss: 0.1880
Epoch 150, Treat Prop: 0.50, Loss: 0.4241
Epoch 200, Treat Prop: 0.02, Loss: 0.0451
Epoch 200, Treat Prop: 0.05, Loss: 0.0707
Epoch 200, Treat Prop: 0.10, Loss: 0.0595
Epoch 200, Treat Pr

 81%|████████▏ | 813/1000 [6:54:12<1:32:46, 29.77s/it]

0.2091100960969925
Seed: 813
Epoch 0, Treat Prop: 0.02, Loss: 4.3570
Epoch 0, Treat Prop: 0.05, Loss: 0.6637
Epoch 0, Treat Prop: 0.10, Loss: 1.4995
Epoch 0, Treat Prop: 0.25, Loss: 3.7174
Epoch 0, Treat Prop: 0.50, Loss: 6.9621
Epoch 50, Treat Prop: 0.02, Loss: 0.2765
Epoch 50, Treat Prop: 0.05, Loss: 0.2931
Epoch 50, Treat Prop: 0.10, Loss: 0.2458
Epoch 50, Treat Prop: 0.25, Loss: 0.4159
Epoch 50, Treat Prop: 0.50, Loss: 1.3636
Epoch 100, Treat Prop: 0.02, Loss: 0.2231
Epoch 100, Treat Prop: 0.05, Loss: 0.2571
Epoch 100, Treat Prop: 0.10, Loss: 0.1856
Epoch 100, Treat Prop: 0.25, Loss: 0.3145
Epoch 100, Treat Prop: 0.50, Loss: 1.0704
Epoch 150, Treat Prop: 0.02, Loss: 0.0976
Epoch 150, Treat Prop: 0.05, Loss: 0.1814
Epoch 150, Treat Prop: 0.10, Loss: 0.1238
Epoch 150, Treat Prop: 0.25, Loss: 0.1530
Epoch 150, Treat Prop: 0.50, Loss: 0.4662
Epoch 200, Treat Prop: 0.02, Loss: 0.0694
Epoch 200, Treat Prop: 0.05, Loss: 0.0707
Epoch 200, Treat Prop: 0.10, Loss: 0.0781
Epoch 200, Treat Pro